The following code verifies equation (6) in Tatsuyuki Hikita's preprint https://arxiv.org/abs/2410.12758 computationally.

Written by Joshua P. Swanson, 11/12/2024. Run on SageMath 10.2.rc4 for n <= 7.

In [89]:
from sage.combinat.q_analogues import q_int, q_factorial

R = ZZ['q'].fraction_field()
q = R.gen()
Sym = SymmetricFunctions(R)
e = Sym.e()

def X_es_q(es):
    '''Returns e-expansion of X(es; q) as a list of pairs (lambda, c_lambda(es; q)).'''
    hs = es_to_hs(es)
    Gamma = Graph(Gamma_hs(hs))
    X = Sym(Gamma.chromatic_quasisymmetric_function().to_symmetric_function())
    return list(e(X)) # e-expansion of \Gamma_e

def es_to_hs(es):
    '''Converts from E_n representation to H_n representation.'''
    n = len(es)
    return [n - es[n-1-i] for i in range(len(es))]

def Gamma_hs(hs):
    '''Constructs the digraph associated with the Hessenberg function hs.'''
    return DiGraph({i+1 : range(i+1+1, hs[i]+1) for i in range(len(hs))})

def es_iter(n):
    '''Iterates over all e = [e_1, ..., e_n] where
       0 <= e_i < i and e_i <= e_{i+1}.'''
    for D in DyckWords(n):
        yield [x-1 for x in D.to_non_decreasing_parking_function()]

In [90]:
def delta_T_r(T, r):
    '''If T is in SYT(n) and 0 <= r <= n, computes
       the color sequence (delta_1, ..., delta_{n+1}).'''
    Tp = T.conjugate()
    ret = []
    for row in Tp:
        ret.append(1 if row[-1] > r else 0)
    ret += [0]*(T.size() + 1 - len(ret))
    return ret

def a_b_l(delta):
    '''A 0,1-sequence delta ending with 0 can be written uniquely as
         delta = (1^{b_0}, 0^{a_1}, 1^{b_1}, ..., 0^{a_l}, 1^{b_l}, 0^{a_{l+1}})
       for b_0 >= 0, a_i, b_i > 0 for i > 0, and some l. Returns (a, b, l)
       where a = [0, a_1, ..., a_{l+1}], b = [b_0, b_1, ..., b_l].'''
    a = [0]
    b = [0]
    prev = 1
    for d in delta:
        if d < prev: # went from 1 to 0
            a.append(1)
        elif d > prev: # went from 0 to 1
            b.append(1)
        elif d==1: # stayed at 1
            b[-1] += 1
        elif d==0: # stayed at 0
            a[-1] += 1
        prev = d
    return (a, b, len(b)-1)

def phi_a_b_l(a, b, l):
    '''Takes the input of a_b_l and computes transition weights (5).'''
    ret = []
    for k in range(l+1):
        g = q^sum(a[1:k+1])
        g *= prod( q_int(sum(a[i+1:k+1]) + sum(b[i:k+1]), q) / q_int(sum(a[i:k+1]) + sum(b[i:k+1]), q) for i in range(1, k+1))
        g *= prod( q_int(sum(a[k+1:i+1]) + sum(b[k+1:i]), q) / q_int(sum(a[k+1:i+1]) + sum(b[k+1:i+1]), q) for i in range(k+1, l+1))
        ret.append(g)
    return tuple(ret)

@cached_method
def f_phi_T_r(T, r):
    '''If T in SYT(n) and 0 <= r <= n, computes the sequence
       f = [f_0, f_1, ..., f_l] where f_k is obtained from T by
       adding a box labeled n+1 to the c_k'th column as in (4),
       as well as the transition probabilities
       phi = [phi_0, phi_1, ..., phi_l]. Returns the tuple
       of pairs ((f_0, phi_0), ..., (f_l, phi_l)).'''
    a,b,l = a_b_l(delta_T_r(T, r))
    c_T_r = [1 + b[0]]
    for k in range(1,l+1):
        c_T_r.append(c_T_r[-1] + a[k] + b[k])
    
    n = T.size()
    la_p = list(T.shape().conjugate()) + [0]
    f = [T.add_entry((la_p[c-1], c-1), n+1) for k,c in enumerate(c_T_r)]
    
    phi = phi_a_b_l(a,b,l)
    return tuple(zip(f, phi))

#@cached_method
def p_T_es(T, es):
    '''If T in SYT(n) and es = [e_1, ..., e_n] where
       0 <= e_i < i, computes p_T(e; q) using Def. 2.'''
    n = T.size()
    if n==0:
        return 1+0*q
    r = es[-1]
    Tp = T.restrict(n-1)
    f_phi = f_phi_T_r(Tp, r)
    for f,phi in f_phi:
#        print(f, T, es)
        if f==T:
            return phi*p_T_es(Tp, es[:-1])
    return 0+0*q

def p_la_es(la, es):
    '''If la is a partition of n and es is as in p_T_es, computes
       p_la(e; q) = sum_{T in SYT(la)} p_T(e; q).'''
    return sum(p_T_es(T, es) for T in StandardTableaux(la) )

def pp_la_es_X(la, es, X):
    '''If la is a partition of n and es is in E_n, renormalizes X as in Hikita's (2).'''
    e_size = sum(es)
    e_la_size = sum( la[i] * la[j] for i in range(len(la)) for j in range(i+1, len(la)) )
    return q^(e_size - e_la_size) * X / prod(q_factorial(la_i, q) for la_i in la)

In [81]:
c = 0
for es in es_iter(7):
    for la,X_la_es in X_es_q(es):
        pp_la_es =  pp_la_es_X(la, es, X_la_es)
        if p_la_es(la, es) != pp_la_es:
            print("FAILURE!", la, es, p_la_es(la, es), pp_la_es)
    c += 1
    if c%10==0:
        print(c)
print("Done.")

10
20
30
40
50
60
70
80
90
100
110
120
130
140
150
160
170
180
190
200
210
220
230
240
250
260
270
280
290
300
310
320
330
340
350
360
370
380
390
400
410
420
Done.


In [94]:
c = 0
for es in es_iter(7):
    c += 1
    if c == 215: # arbitrary Hessenberg-like function
        print(es)
        la,X_la_es = choice(X_es_q(es))    # pick some non-zero e_lambda coefficient
        print(la)                          # shape
        print(X_la_es)                     # coefficient
        print(pp_la_es_X(la, es, X_la_es)) # renormalized coefficient
        print(p_la_es(la, es))             # RHS of Hikita's (6), which is asserted to equal the above coefficient up to normalization


[0, 0, 1, 2, 2, 2, 3]
[7]
q^11 + 4*q^10 + 9*q^9 + 14*q^8 + 17*q^7 + 18*q^6 + 18*q^5 + 17*q^4 + 14*q^3 + 9*q^2 + 4*q + 1
q^10/(q^10 + 2*q^9 + 3*q^8 + 5*q^7 + 6*q^6 + 6*q^5 + 6*q^4 + 5*q^3 + 3*q^2 + 2*q + 1)
q^10/(q^10 + 2*q^9 + 3*q^8 + 5*q^7 + 6*q^6 + 6*q^5 + 6*q^4 + 5*q^3 + 3*q^2 + 2*q + 1)


In [95]:
f_phi_T_r(StandardTableau([[1, 2, 3, 6], [4, 5]]), 4) # Reproduce Hikita's Figure 1

(([[1, 2, 3, 6], [4, 5], [7]], (q^2 + q + 1)/(q^4 + 2*q^3 + 2*q^2 + 2*q + 1)),
 ([[1, 2, 3, 6], [4, 5, 7]], q/(q^2 + 2*q + 1)),
 ([[1, 2, 3, 6, 7], [4, 5]],
  (q^4 + q^3 + q^2)/(q^4 + 2*q^3 + 2*q^2 + 2*q + 1)))